# Loading the Data

In [42]:
# load data

# import the experiment utilities package
import exputils as eu
import numpy as np

# create an experiment data loader, by default it will load data from '../experiments'
experiment_data_loader = eu.gui.jupyter.ExperimentDataLoaderWidget()

display(experiment_data_loader)
experiment_data_loader.load_data()

ExperimentDataLoaderWidget(children=(Box(children=(Button(description='Update Descriptions', layout=Layout(hei…

Output()

# Check for Data Completeness

In [2]:
import dill
from pmlb import fetch_data

experiment_data_loader.experiment_data["000001"]["repetition_data"][0].keys()

data_dir = "../experiments/experiment_000001/repetition_000000/data/"

with open(data_dir+"dataset.dill", 'rb') as data:
    dataset_names = dill.load(data)

print(dataset_names)

for dataset_name in dataset_names:
    X,Y = fetch_data(dataset_name, return_X_y=True)
    print(f"{dataset_name}: x -> {X.shape}")

['1027_ESL', '1028_SWD', '1029_LEV', '1030_ERA', '1096_FacultySalaries', '1193_BNG_lowbwt', '1196_BNG_pharynx', '1199_BNG_echoMonths', '1201_BNG_breastTumor', '1203_BNG_pwLinear', '1595_poker', '192_vineyard', '210_cloud', '215_2dplanes', '218_house_8L', '225_puma8NH', '228_elusage', '229_pwLinear', '230_machine_cpu', '344_mv', '485_analcatdata_vehicle', '519_vinnie', '522_pm10', '523_analcatdata_neavote', '529_pollen', '537_houses', '547_no2', '556_analcatdata_apnea2', '557_analcatdata_apnea1', '561_cpu', '564_fried', '579_fri_c0_250_5', '591_fri_c1_100_10', '593_fri_c1_1000_10', '594_fri_c2_100_5', '595_fri_c0_1000_10', '596_fri_c2_250_5', '597_fri_c2_500_5', '599_fri_c2_1000_5', '601_fri_c1_250_5', '602_fri_c3_250_10', '604_fri_c4_500_10', '606_fri_c2_1000_10', '608_fri_c3_1000_10', '609_fri_c0_1000_5', '611_fri_c3_100_5', '612_fri_c1_1000_5', '613_fri_c3_250_5', '615_fri_c4_250_10', '617_fri_c3_500_5', '621_fri_c0_100_10', '623_fri_c4_1000_10', '624_fri_c0_100_5', '627_fri_c2_500_1

# Plotting the Data

In [2]:
## experiment data selection plotter that takes as input the data loader to plot its loaded data
experiment_data_plotter = eu.gui.jupyter.ExperimentDataPlotSelectionWidget(experiment_data_loader)
display(experiment_data_plotter)

ExperimentDataPlotSelectionWidget(children=(HBox(children=(Label(value='Data Sources:', layout=Layout(min_widt…

In [3]:
### Execution time


In [43]:
import os
import dill

def load_experiment_data(experiment_num):
    num_str = "%06d" % experiment_num
    #repetition_str = "%06d" % repetition_num


    base_dir = "../experiments/experiment_"+num_str+"/"
    data_dir = "../experiments/experiment_"+num_str+"/repetition_000000/data/"

    with open(data_dir+"dataset.dill", 'rb') as data:
        datasets = dill.load(data)


    means = {}
    stds = {}

    train_loss = {}
    test_loss = {}
    val_loss = {}

    # Iterate over each entry in the given path
    for repetition_entry in os.listdir(base_dir):
        # Create full path
        repetition_path = os.path.join(base_dir, repetition_entry)

        if not os.path.isdir(repetition_path):
            continue


        for dataset_entry in os.listdir(repetition_path):
            dataset_path = os.path.join(repetition_path, dataset_entry)
            if os.path.isdir(dataset_path) and "data" in dataset_entry and dataset_entry != "data":
                dataset_name = dataset_entry[4:]

                if dataset_name not in means:
                    means[dataset_name] = []
                    stds[dataset_name] = []
                    train_loss[dataset_name] = []
                    test_loss[dataset_name] = []
                    val_loss[dataset_name] = []

                _rep_dataset_means = []
                _rep_dataset_stds = []

                _test_loss = None
                _train_loss = None
                _val_loss = None

                for data_entry in os.listdir(dataset_path):
                
                    try:
                        data_path = os.path.join(dataset_path, data_entry)

                        if "mean" in data_entry and data_entry[0] != ".":
                            mean = np.load(data_path)
                            _rep_dataset_means.append(mean)

                        if "std" in data_entry and data_entry[0] != ".":
                            std = np.load(data_path)
                            _rep_dataset_stds.append(std)

                        if "train_loss" in data_entry and data_entry[0] != ".":
                            _train_loss = np.load(data_path)

                        if "test_loss" in data_entry and data_entry[0] != ".":
                            _test_loss = np.load(data_path)

                        if "val_loss" in data_entry and data_entry[0] != ".":
                            _val_loss = np.load(data_path)
                    except:
                        print(f"Error at retrieving data for: {data_entry}")

                if len(_rep_dataset_means) > 0:
                    _rep_dataset_means = np.stack(_rep_dataset_means)

                if len(_rep_dataset_stds) > 0:
                    _rep_dataset_stds = np.stack(_rep_dataset_stds)

                means[dataset_name].append(_rep_dataset_means)
                stds[dataset_name].append(_rep_dataset_stds)
                train_loss[dataset_name].append(_train_loss)
                test_loss[dataset_name].append(_test_loss)
                val_loss[dataset_name].append(_val_loss)


    for key,val in means.items():
        try:
            means[key] = np.stack(val).transpose((0,2,1))
            #print(f"loaded means {means[key].shape}")
        except:
            pass
            print("Not present")

    for key,val in stds.items():
        try:
            stds[key] = np.stack(val).transpose((0,2,1))
            #print(f"loaded stds {stds[key].shape}")
        except:
            print("Not present")

    for key,val in train_loss.items():
        try:
            train_loss[key] = np.stack(val).transpose((1,0))
            #print(f"loaded train {train_loss[key].shape}")
        except:
            print("Not present")

    for key,val in test_loss.items():
        try:
            test_loss[key] = np.stack(val).transpose((1,0))
            #print(f"loaded test {test_loss[key].shape}")
        except:
            print("Not present") 

    for key,val in val_loss.items():
        try:
            val_loss[key] = np.stack(val).transpose((1,0))
            #print(f"loaded val {val_loss[key].shape}")
        except:
            print("Not present")


            
    return means, stds, train_loss, test_loss, val_loss
    
means, stds, train_loss, test_loss, val_loss = load_experiment_data(15)   



Error at retrieving data for: mean149.npy


In [ ]:
dataset_name = "1096_FacultySalaries"

## Mean value

In [ ]:
## plotting
import numpy as np
import plotly.graph_objects as go




data = means[dataset_name][0]

print(data.shape)

# Preparing data for plotting
epochs = np.arange(1, data.shape[0])
traces = []
for i in range(data.shape[1]):
    traces.append(go.Scatter(x=epochs, y=data[:, i], mode='lines', name=f'Value {i+1}'))

# Plotting with Plotly
layout = go.Layout(title='Change of 16 Values over 500 Steps',
                   xaxis=dict(title='Epoch'),
                   yaxis=dict(title='Value'),
                   template='plotly_dark')

fig = go.Figure(data=traces, layout=layout)
fig.show()



## StandardDeviation Values

In [ ]:
### plot
import numpy as np
import plotly.graph_objects as go


data = stds[dataset_name][0]
    
# Preparing data for plotting
epochs = np.arange(1, data.shape[0])
traces = []
for i in range(data.shape[1]):
    traces.append(go.Scatter(x=epochs, y=data[:, i], mode='lines', name=f'Value {i+1}'))

# Plotting with Plotly
layout = go.Layout(title='Change of 16 Values over 500 Steps',
                   xaxis=dict(title='Epoch'),
                   yaxis=dict(title='Value'),
                   template='plotly_dark')

fig = go.Figure(data=traces, layout=layout)
fig.show()

In [6]:
### plot
import numpy as np
import plotly.graph_objects as go


data = test_loss[dataset_name]
    
# Preparing data for plotting
epochs = np.arange(1, data.shape[0])
traces = []


data = np.expand_dims(data.mean(axis = 1), axis = 1)

for i in range(data.shape[1]):
    traces.append(go.Scatter(x=epochs, y=data[:, i], mode='lines', name=f'Value {i+1}'))
    


# Plotting with Plotly
layout = go.Layout(title='Change of 16 Values over 500 Steps',
                   xaxis=dict(title='Epoch'),
                   yaxis=dict(title='Value'),
                   template='plotly_dark')

fig = go.Figure(data=traces, layout=layout)
fig.show()

NameError: name 'dataset_name' is not defined

In [7]:
### plot
import numpy as np
import plotly.graph_objects as go


data = val_loss[dataset_name]
    
# Preparing data for plotting
epochs = np.arange(1, data.shape[0])
traces = []


data = np.expand_dims(data.mean(axis = 1), axis = 1)

for i in range(data.shape[1]):
    traces.append(go.Scatter(x=epochs, y=data[:, i], mode='lines', name=f'Value {i+1}'))
    


# Plotting with Plotly
layout = go.Layout(title='Change of 16 Values over 500 Steps',
                   xaxis=dict(title='Epoch'),
                   yaxis=dict(title='Value'),
                   template='plotly_dark')

fig = go.Figure(data=traces, layout=layout)
fig.show()

NameError: name 'dataset_name' is not defined

In [44]:
import numpy as np
import matplotlib.pyplot as plt
import traceback 

max_method_num = 48

min_test_loss = {}
min_val_test_loss = {}

for i in range(1,max_method_num):
    means, stds, train_loss, test_loss, val_loss = load_experiment_data(i)    
    for dataset in list(train_loss.keys()):
        print(f"Analyzing: {dataset} {i}")
        
        try:
            rep_min_test_loss = np.min(np.mean(test_loss[dataset],axis = 1),axis=0)
            idx_min_val_loss = np.argmin(np.mean(val_loss[dataset],axis = 1),axis=0)
            
            if dataset not in min_test_loss:
                min_test_loss[dataset] = {}
                
            if dataset not in min_val_test_loss:
                min_val_test_loss[dataset] = {}

            min_test_loss[dataset][i] = rep_min_test_loss
            min_val_test_loss[dataset][i] = np.mean(test_loss[dataset],axis = 1)[idx_min_val_loss]
            
            print(np.mean(test_loss[dataset],axis = 1)[idx_min_val_loss])
        except: 
            traceback.print_exc() 

### remove all inclompete datasets...
to_delete = []
for key, val in min_test_loss.items():
    if len(val.keys()) < max_method_num - 1:
        print(f"For {key} not all datasets present {len(val.keys())}")
        to_delete.append(key)


#for key in to_delete:
#    del min_test_loss[key]
#    del min_val_test_loss[key]
        
### Calculate with reference to specific method
reference_method = 4

# Calculate relative min test loss
relative_min_test_loss = {}
relative_min_val_test_loss = {}

for dataset_name, dataset_vals in min_test_loss.items():
    relative_min_test_loss[dataset_name] = {method: val / dataset_vals[reference_method] for method, val in dataset_vals.items()}

for dataset_name, dataset_vals in min_val_test_loss.items():    
    relative_min_val_test_loss[dataset_name] = {method: val / dataset_vals[reference_method] for method, val in dataset_vals.items()}    


#full_relative_min_test_loss = {}
        

Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not 

Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not 

Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not 

Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Not present
Analyzing: 215_2dplanes 7
17.482748925685883
Analyzing: 344_mv 7
0.2378137685591355
Analyzing: 522_pm10 7
0.7763468623161316
Analyzing: 

Traceback (most recent call last):
  File "/var/folders/vx/2hn3fq3j01ndcrt24ck57sr80000gn/T/ipykernel_55969/2211522739.py", line 16, in <module>
    rep_min_test_loss = np.min(np.mean(test_loss[dataset],axis = 1),axis=0)
                               ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "<__array_function__ internals>", line 200, in mean
  File "/opt/homebrew/lib/python3.11/site-packages/numpy/core/fromnumeric.py", line 3464, in mean
    return _methods._mean(a, axis=axis, dtype=dtype,
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/opt/homebrew/lib/python3.11/site-packages/numpy/core/_methods.py", line 165, in _mean
    arr = asanyarray(a)
          ^^^^^^^^^^^^^
ValueError: setting an array element with a sequence. The requested array has an inhomogeneous shape after 1 dimensions. The detected shape was (4,) + inhomogeneous part.


...

Analyzing: 522_pm10 31
1.1409715215365093
Analyzing: 519_vinnie 31
2.5097551345825195
Analyzing: 485_analcatdata_vehicle 31
36553.6171875
Analyzing: 1030_ERA 31
5.111788749694824
Analyzing: 229_pwLinear 31
2.894187053044637
Analyzing: 1027_ESL 31
0.32335884869098663
Analyzing: 523_analcatdata_neavote 31
1.2447632948557537
Analyzing: 529_pollen 31
14.921783556540808
Analyzing: 230_machine_cpu 31
6856.9375
Analyzing: 1196_BNG_pharynx 31
1356160.05859375
Analyzing: 1193_BNG_lowbwt 31
3491360.484375
Analyzing: 228_elusage 31
152.9754638671875
Analyzing: 1096_FacultySalaries 31
3.732674539089203
Analyzing: 1029_LEV 31
0.674577109515667
Analyzing: 210_cloud 31
0.2505562845617533
Analyzing: 192_vineyard 31
6.2688629031181335
Analyzing: 1028_SWD 31
0.8185873851180077
Analyzing: 225_puma8NH 31
134.1796785990397
Analyzing: 1199_BNG_echoMonths 31
2184.0623575846353
Analyzing: 215_2dplanes 31
17.016924560070038
Analyzing: 635_fri_c0_250_10 31
0.1448167935013771
Analyzing: 344_mv 31
75.196888446807

Traceback (most recent call last):
  File "/var/folders/vx/2hn3fq3j01ndcrt24ck57sr80000gn/T/ipykernel_55969/2211522739.py", line 16, in <module>
    rep_min_test_loss = np.min(np.mean(test_loss[dataset],axis = 1),axis=0)
                               ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "<__array_function__ internals>", line 200, in mean
  File "/opt/homebrew/lib/python3.11/site-packages/numpy/core/fromnumeric.py", line 3464, in mean
    return _methods._mean(a, axis=axis, dtype=dtype,
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/opt/homebrew/lib/python3.11/site-packages/numpy/core/_methods.py", line 165, in _mean
    arr = asanyarray(a)
          ^^^^^^^^^^^^^
ValueError: setting an array element with a sequence. The requested array has an inhomogeneous shape after 1 dimensions. The detected shape was (4,) + inhomogeneous part.


Analyzing: 635_fri_c0_250_10 34
0.19292369484901428
Analyzing: titanic 34
0.545440386980772
Analyzing: 522_pm10 34
0.61826092004776
Analyzing: 556_analcatdata_apnea2 34
2809614.625
Analyzing: 631_fri_c1_500_5 34
0.05186521075665951
Analyzing: 634_fri_c2_100_10 34
0.1322285532951355
Analyzing: 615_fri_c4_250_10 34
0.14239810779690742
Analyzing: 601_fri_c1_250_5 34
0.05253375507891178
Analyzing: 537_houses 34
34891656640.0
Analyzing: 519_vinnie 34
2.7343332767486572
Analyzing: 561_cpu 34
4079.721336364746
Analyzing: 485_analcatdata_vehicle 34
17520.9814453125
Analyzing: 613_fri_c3_250_5 34
0.07757624238729477
Analyzing: 1030_ERA 34
5.263519704341888
Analyzing: 595_fri_c0_1000_10 34
0.17196985334157944
Analyzing: 597_fri_c2_500_5 34
0.05724724009633064
Analyzing: 229_pwLinear 34
3.356437623500824
Analyzing: 712_chscase_geyser1 34
48.25531578063965
Analyzing: 647_fri_c1_250_10 34
0.10927857458591461
Analyzing: 1027_ESL 34
0.3672051876783371
Analyzing: 593_fri_c1_1000_10 34
0.14026727154850

Analyzing: 635_fri_c0_250_10 37
1.1865901350975037
Analyzing: titanic 37
0.545675091445446
Analyzing: 522_pm10 37
0.7688601811726888
Analyzing: 556_analcatdata_apnea2 37
nan
Analyzing: 631_fri_c1_500_5 37
0.7516882717609406
Analyzing: 634_fri_c2_100_10 37
0.8868992924690247
Analyzing: 615_fri_c4_250_10 37
0.8428870737552643
Analyzing: 601_fri_c1_250_5 37
1.0017797350883484
Analyzing: 537_houses 37
65296954368.0
Analyzing: 519_vinnie 37
2.700770616531372
Analyzing: 561_cpu 37
1694.6038208007812
Analyzing: 485_analcatdata_vehicle 37
nan
Analyzing: 613_fri_c3_250_5 37
0.6602112948894501
Analyzing: 1030_ERA 37
5.82902455329895
Analyzing: 595_fri_c0_1000_10 37
1.0999084897339344
Analyzing: 597_fri_c2_500_5 37
0.16939765959978104
Analyzing: 229_pwLinear 37
16.663992245992024
Analyzing: 712_chscase_geyser1 37
34.254995346069336
Analyzing: 647_fri_c1_250_10 37
0.6655740439891815
Analyzing: 1027_ESL 37
0.2914775088429451
Analyzing: 593_fri_c1_1000_10 37
1.9635255336761475
Analyzing: 523_analcat

Analyzing: 215_2dplanes 40
17.133591294288635
Analyzing: 635_fri_c0_250_10 40
0.18179314583539963
Analyzing: 344_mv 40
0.008536894703865983
Analyzing: titanic 40
0.5809832289814949
Analyzing: 522_pm10 40
5.459677308797836
Analyzing: 556_analcatdata_apnea2 40
8299291.0
Analyzing: 631_fri_c1_500_5 40
0.061281561851501465
Analyzing: 634_fri_c2_100_10 40
0.13624386489391327
Analyzing: 615_fri_c4_250_10 40
0.12893661484122276
Analyzing: 601_fri_c1_250_5 40
0.0732157900929451
Analyzing: 537_houses 40
67915296000.0
Analyzing: 519_vinnie 40
2.765401244163513
Analyzing: 561_cpu 40
26388.794921875
Analyzing: 485_analcatdata_vehicle 40
99394.279296875
Analyzing: 613_fri_c3_250_5 40
0.08361708000302315
Analyzing: 595_fri_c0_1000_10 40
0.15776490420103073
Analyzing: 597_fri_c2_500_5 40
0.05179882235825062
Analyzing: 229_pwLinear 40
3.2983418703079224
Analyzing: 712_chscase_geyser1 40
64.73325729370117
Analyzing: 647_fri_c1_250_10 40
0.10671282932162285
Analyzing: 1027_ESL 40
0.34195148944854736
Ana

In [45]:
import plotly.graph_objects as go
import plotly.express as px

colors = px.colors.qualitative.Plotly

colors = [*colors,*colors,*colors,*colors]

dataset_names = list(min_test_loss.keys())

for dataset_name in dataset_names:
    # Extract methods and corresponding test losses for the current dataset
    methods = list(relative_min_test_loss[dataset_name].keys())
    test_losses = [relative_min_test_loss[dataset_name][method] for method in methods]

    # Create a bar chart for the current dataset
    fig = go.Figure(data=[
        go.Bar(
            x=methods,
            y=test_losses,
            name=dataset_name,
            marker_color=colors[:len(methods)]  # Assign different colors to each bar
        )
    ])

    print(methods)
    
    # Customize the layout
    fig.update_layout(
        title=f'Relative Min Test Loss by Method for {dataset_name}',
        xaxis=dict(
            title='Method',
            #tickmode='array',
            #tickvals=list(range(len(methods))),
            #ticktext=methods
        ),
        yaxis=dict(
            title='Relative Min Test Loss'
        ),
        legend_title=dataset_name
        # Additional customizations can be added here
    )

    # Show the plot
    fig.show()

[1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 27, 28, 29, 31, 32, 36, 40]


[1, 2, 3, 4, 5, 6, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40]


[1, 2, 3, 4, 5, 6, 7, 9, 10, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 37, 40]


[1, 2, 3, 4, 5, 6, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40]


[1, 2, 3, 4, 5, 6, 7, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40]


...

[1, 2, 3, 4, 5, 6, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40]


[1, 2, 3, 4, 5, 6, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40]


[1, 2, 3, 4, 5, 6, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40]


[1, 2, 3, 4, 5, 6, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40]


[1, 2, 3, 4, 5, 6, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40]


In [46]:

dataset_names = list(min_val_test_loss.keys())

for dataset_name in dataset_names:
    # Preparing data for bar chart
    methods = list(relative_min_val_test_loss[dataset_name].keys())
    test_losses = [relative_min_val_test_loss[dataset_name][method] for method in methods]


    # Create a bar chart for the current dataset
    fig = go.Figure(data=[
        go.Bar(
            x=methods,
            y=test_losses,
            name=dataset_name,
            marker_color=colors[:len(methods)]  # Assign different colors to each bar
        )
    ])

    # Customize the layout
    fig.update_layout(
        title=f'Relative Min Test Loss by Method for {dataset_name}',
        xaxis=dict(
            title='Method',
        ),
        yaxis=dict(
            title='Relative Min Test Loss'
        ),
        legend_title=dataset_name
        # Additional customizations can be added here
    )

    # Show the plot
    fig.show()
    

In [47]:
### The mean over all datasets is not a good indicator!! (Prone to outliers) Every dataset has different properties and therefore different methods perform best.

import plotly.express as px

dataset_names = list(min_val_test_loss.keys())

summary_test_loss = {}


for dataset_name, dataset_vals in relative_min_val_test_loss.items():
    for method_name, method_val in dataset_vals.items():
        if method_name not in summary_test_loss:
            summary_test_loss[method_name] = []
        
        summary_test_loss[method_name].append(method_val)
        
for method_name, method_vals in summary_test_loss.items():
    summary_test_loss[method_name] = np.mean(method_vals)


# Adding bars for each dataset
methods = list(summary_test_loss.keys())
index = np.arange(len(methods))  # the label locations

test_losses = [summary_test_loss[method] for method in methods]
dataset_name = "summary"
# Create a bar chart for the current dataset
fig = go.Figure(data=[
    go.Bar(
        x=methods,
        y=test_losses,
        name=dataset_name,
        marker_color = colors[:len(methods)]  # Assign different colors to each bar
    )
])

# Customize the layout
fig.update_layout(
    title=f'Relative Min Test Loss by Method for {dataset_name}',
    xaxis=dict(
        title='Method',
        #tickmode='array',
        tickvals=list(range(len(methods))),
        ticktext=methods
    ),
    yaxis=dict(
        title='Relative Min Test Loss'
    ),
    legend_title=dataset_name
    # Additional customizations can be added here
)

# Show the plot
fig.show()


In [48]:
import plotly.graph_objects as go
import numpy as np

dataset_names = list(relative_min_val_test_loss.keys())
methods = list(set([method for dataset in relative_min_val_test_loss.values() for method in dataset.keys()]))

# Prepare data for heatmap
heatmap_data = []
best_methods_indices = []

for dataset in dataset_names:
    dataset_vals = []
    best_loss = float('inf')
    best_method_index = -1

    for index, method in enumerate(methods):
        loss = relative_min_val_test_loss[dataset].get(method, None)
        
        if loss is not None: ### only used to get a clearer contrast between low value scores..
            loss = min(100,loss)
        
        dataset_vals.append(loss)

        if loss is not None and loss < best_loss:
            best_loss = loss
            best_method_index = index
    
    heatmap_data.append(dataset_vals)
    best_methods_indices.append(best_method_index)

# Create the heatmap
fig = go.Figure(data=go.Heatmap(
    z=heatmap_data,
    x=methods,
    y=dataset_names,
    colorscale='Turbo'
))

# Overlay with scatter plot to highlight the best methods
for i, best_index in enumerate(best_methods_indices):
    fig.add_trace(go.Scatter(
        x=[methods[best_index]],
        y=[dataset_names[i]],
        mode='markers',
        marker=dict(
            color='red',
            size=4,
            line=dict(
                color='red',
                width=1
                
            )
        )
    ))

# Customize layout
fig.update_layout(
    title='Relative Min Test Loss by Method and Dataset',
    xaxis=dict(title='Method'),
    yaxis=dict(title='Dataset'),
    showlegend=False
)

# Show the plot
fig.show()


In [49]:
import plotly.graph_objects as go

# Assuming 'relative_min_val_test_loss' and 'dataset_names' are defined as before
dataset_names = list(relative_min_val_test_loss.keys())

# Finding methods across all datasets
methods = list(set([method for dataset_vals in relative_min_val_test_loss.values() for method in dataset_vals.keys()]))

# Initialize x, y, z for 3D scatter plot locations and test losses for color scale
x, y, z, test_losses = [], [], [], []

for i, dataset in enumerate(dataset_names):
    for j, method in enumerate(methods):
        loss = relative_min_val_test_loss[dataset].get(method)
        if loss is not None:
            x.append(j)  # method index
            y.append(i)  # dataset index
            z.append(loss)  # test loss
            test_losses.append(loss)

# Create 3D scatter plot with a continuous color scale
fig = go.Figure(data=[go.Scatter3d(
    x=x,
    y=y,
    z=z,
    mode='markers',
    marker=dict(
        size=5,
        color=test_losses,  # Assign color based on test loss
        colorscale='Viridis',  # Choose a color scale
        colorbar=dict(title='Test Loss'),
        opacity=0.8
    )
)])

# Customize layout
fig.update_layout(
    scene=dict(
        xaxis=dict(title='Method', tickvals=list(range(len(methods))), ticktext=methods),
        yaxis=dict(title='Dataset', tickvals=list(range(len(dataset_names))), ticktext=dataset_names),
        zaxis=dict(title='Relative Min Test Loss')
    ),
    title='3D Scatter Plot of Relative Min Test Loss by Method and Dataset'
)

# Show the plot
fig.show()


